In [1]:
import lda
from scipy import sparse
import numpy as np

import json
import gensim 
import sklearn
import sys

unable to import 'smart_open.gcs', disabling that module


In [2]:
from scipy.spatial.distance import jensenshannon

In [3]:
from heapq import heappush, heappushpop

In [4]:
X_train = sparse.load_npz('/Users/tingchen/Desktop/Yelp Project/data_n_20_removed_all_eths_minus_american/X_train.npz')
cc= np.load("/Users/tingchen/Desktop/Yelp Project/data_n_20_removed_all_eths_minus_american/y_train.npy")
locs = []
with open("/Users/tingchen/Desktop/Yelp Project/data_n_20_removed_all_eths_minus_american/locs_train.json", 'r') as file:
    locs = json.load(file)

In [10]:
cc.shape

(2058609, 1)

In [5]:
ix = X_train.getnnz(1)>0
X_train = X_train[ix]
cc= cc[ix]
locs= np.array(locs)[ix]

In [13]:
# locations of each ethnicity
locs_eth = [[] for eth in range(len(set(cc[:,0])))]
indicies_locs_eth = []

for i, c in enumerate(cc[:,0]):
    locs_eth[c].append(locs[i])
    indicies_locs_eth.append(len(locs_eth[c]) -1)

## Automate determination of regions

In [14]:
#dpgmm_eth = []

n_regions = []

eth_regions = [[] for eth in range(len(set(cc[:, 0])))] # assignments of regions for each ethnicity

for i in range(len(set(cc[:, 0]))):
    regions = 10
    converged = False
    
    while not converged: 
        dpgmm = sklearn.mixture.BayesianGaussianMixture(verbose=0, n_components=regions, max_iter=500)
        pred = dpgmm.fit_predict(locs_eth[i]).tolist()
 
        if all(i >= 0.005 for i in dpgmm.weights_):
            converged = True
            eth_regions[i] = pred
            n_regions.append(regions)
        else:
            regions += -1

## Train model

In [15]:
reg_assign = []

for i, elem in enumerate(eth_regions):
    reg_assign.append(np.array(elem, dtype=np.intc))

In [16]:
max_len = max([x.shape[0] for x in reg_assign])

In [17]:
reg_assign_mat = np.zeros((len(reg_assign), max_len), dtype = np.intc) # region assignment by cuisines and number on loc

In [18]:
for i, row in enumerate(reg_assign):
    reg_assign_mat[i, :len(row)] += row

In [19]:
indicies_locs_eth = np.array(indicies_locs_eth, dtype=np.intc) # placement in region index for each loc 

In [21]:
cc = cc[:,0]

In [22]:
#first = 10000

model = lda.LDA(n_topics= 25, region_assignments=reg_assign_mat, n_regions_fluid = n_regions, indices_region_assignments=indicies_locs_eth, n_iter=1000)
model.fit_fluid(X_train.astype(np.int), cc.astype(np.int32), locs)

all zero column in document-term matrix found
  0%|          | 0/1000 [00:00<?, ?it/s]

Finished initializing


100%|██████████| 1000/1000 [8:55:50<00:00, 32.15s/it] 


Burnin finished
done with topic word and doc topic
done with topic_word_regions


In [40]:
del model

## Testing Jensen Shannon calculations

In [23]:
np.save("./model_persistence/all_eths_less_than_15000_minus_american_1000_its_25_topics/nzwcr.npy", model.nzwcr_)

In [24]:
np.save("./model_persistence/all_eths_less_than_15000_minus_american_1000_its_25_topics/nzw.npy", model.nzw_)

In [25]:
np.save("./model_persistence/all_eths_less_than_15000_minus_american_1000_its_25_topics/ndz.npy", model.ndz_)

In [26]:
np.save("./model_persistence/all_eths_less_than_15000_minus_american_1000_its_25_topics/reg_assign_mat.npy", reg_assign_mat)

In [27]:
np.save("./model_persistence/all_eths_less_than_15000_minus_american_1000_its_25_topics/indicies_locs_eth.npy", indicies_locs_eth)

In [29]:
collection_word = model.nzwcr_

In [31]:
np.count_nonzero(collection_word[0, :, 0, 1])

0

In [22]:
np.count_nonzero(collection_word)

2350695

In [24]:
# store top  differences in priority queue of tuples (topic, cuisine number, first region, second region)
num_saved = 60 # top saved


top_dists = []

for i in range(num_saved):
    heappush(top_dists, (0.000001 * i, (1, 1, 1, 1)))

Look at difference between different regions within a topic and cuisine

In [25]:
for topic in range(collection_word.shape[0]):
    print("\rtopic: " +str(topic), end="")
    for cuis in range(collection_word.shape[2]):

        test = collection_word[topic, :, cuis, :] +1

        #dists = np.zeros((n_regions[cuis], n_regions[cuis]))

        for reg in range(n_regions[cuis]-1):
            for reg1 in range(reg + 1, n_regions[cuis]):
                dist = jensenshannon(test[:, reg], test[:, reg1])

                if dist > top_dists[0][0]:
                    heappushpop(top_dists, (dist, (topic, cuis, reg, reg1)))

topic: 24

In [26]:
print(*sorted(top_dists, key = lambda entry : entry[0], reverse=True), sep = "\n")

(0.16153814925570417, (6, 1, 0, 4))
(0.15814430440762842, (6, 1, 0, 7))
(0.1577547957032772, (6, 1, 0, 3))
(0.15768626926764767, (6, 1, 0, 8))
(0.15665746680381387, (6, 1, 0, 6))
(0.15616939047378148, (5, 18, 0, 4))
(0.15576930078334336, (6, 1, 0, 2))
(0.15566059544175298, (4, 18, 0, 4))
(0.15226358814547744, (9, 4, 1, 5))
(0.15085378034780805, (6, 1, 1, 4))
(0.14822087241256598, (9, 4, 1, 4))
(0.14803674626722987, (6, 1, 1, 3))
(0.14763205984428157, (6, 1, 1, 6))
(0.1473120214742333, (9, 4, 1, 7))
(0.14682300713312646, (6, 1, 1, 7))
(0.14673028476232558, (6, 1, 1, 8))
(0.1446508717351194, (4, 1, 1, 4))
(0.14394655755511016, (8, 18, 0, 4))
(0.14385335119139125, (6, 1, 1, 2))
(0.14349184543570748, (4, 1, 1, 3))
(0.1427729862029282, (4, 18, 0, 2))
(0.1427596013678908, (4, 1, 1, 6))
(0.1421441548612107, (4, 18, 0, 5))
(0.14181719142903176, (5, 18, 0, 5))
(0.14116354779811313, (4, 1, 1, 8))
(0.14047839369510254, (4, 1, 1, 7))
(0.13908070164047395, (5, 18, 0, 2))
(0.13862477497511344, (7, 1

Look at differences between cuisines within a region

In [31]:
# Marginalize region out of nzwcr

nzwc = np.zeros((model.nzwcr_.shape[:-1]))

for i in range(nzwc.shape[0]):
    print('\rTopic: ', i, end="")
    for j in range(nzwc.shape[1]):
        for k in range(nzwc.shape[2]):
            nzwc[i, j, k] = np.sum(model.nzwcr_[i, j, k, :n_regions[k]])

Topic:  24

In [32]:
np.save("./model_persistence/all_eths_less_than_15000_minus_american_1000_its_25_topics/nzwc.npy", nzwc)

In [22]:
nzwc = np.load("./model_persistence/all_eths_less_than_15000_1000_its_25_topics/nzwc.npy")

In [28]:
top_dists_c = []

for i in range(num_saved):
    heappush(top_dists_c, (0.000001 * i, (1, 1, 1)))

In [29]:
for topic in range(nzwc.shape[0]):
    test = nzwc[topic, :, :] + 1
    for eth in range(nzwc.shape[2] - 1):
        for eth1 in range(eth + 1, nzwc.shape[2]):
            dist = jensenshannon(test[:, eth], test[:, eth1])
            
            if dist > top_dists_c[0][0]:
                    heappushpop(top_dists_c, (dist, (topic, eth, eth1)))

In [30]:
print(*sorted(top_dists_c, key = lambda entry : entry[0], reverse=True), sep = "\n")

(0.30610502108756715, (6, 1, 18))
(0.2983304543456445, (5, 4, 18))
(0.2971350045310963, (5, 1, 18))
(0.29688385627107855, (4, 4, 18))
(0.29125534873886905, (6, 1, 4))
(0.28998975574594466, (4, 1, 18))
(0.2774611710938919, (5, 1, 4))
(0.27621584990164477, (9, 1, 4))
(0.2751627583446533, (4, 1, 4))
(0.27014257273290715, (6, 4, 18))
(0.26979082699454726, (11, 11, 18))
(0.269326475656991, (9, 4, 18))
(0.2691924732397476, (6, 11, 18))
(0.2681361778226873, (8, 4, 18))
(0.26781818732443236, (5, 11, 18))
(0.2673994265151391, (6, 1, 14))
(0.26568881978195497, (8, 1, 18))
(0.26532402313113496, (4, 11, 18))
(0.26253328706439266, (11, 1, 18))
(0.26218476236468885, (11, 1, 20))
(0.259245516465613, (11, 1, 11))
(0.2592439592322965, (6, 1, 11))
(0.25907175100633134, (6, 1, 2))
(0.25772388634853644, (7, 1, 18))
(0.25728709810401545, (6, 1, 9))
(0.25707378911372664, (5, 14, 18))
(0.25657763736076183, (6, 1, 24))
(0.25608851221519274, (6, 1, 8))
(0.2549159595643124, (6, 1, 10))
(0.25481351129527463, (6,

## Find biggest differences with American cuisines

In [14]:
num_saved = 60 # top saved

In [38]:
top_dists_c = []

for i in range(num_saved):
    heappush(top_dists_c, (-1 * i, (1, 1)))

In [39]:
base = 10 # American Traditional
base_1 = 15 # American_new

for topic in range(nzwc.shape[0]):
    test = nzwc[topic, :, :] + 1
    for eth in range(nzwc.shape[2]):
        dist = -1*jensenshannon(test[:, eth], test[:, base])
            
        if dist > top_dists_c[0][0]:
            heappushpop(top_dists_c, (dist, (topic, eth)))

In [40]:
top_dists_c[0]

(-0.05615086210875529, (21, 0))

In [41]:
print(*sorted(top_dists_c, key = lambda entry : entry[0], reverse=True), sep = "\n")

(-0.0, (16, 10))
(-0.0, (1, 10))
(-0.0, (5, 10))
(-0.0, (23, 10))
(0, (1, 1))
(-0.0, (6, 10))
(-0.0, (8, 10))
(-0.0, (15, 10))
(-0.0, (10, 10))
(-0.0, (18, 10))
(-0.0, (7, 10))
(-0.0, (19, 10))
(-0.0, (24, 10))
(-0.0, (20, 10))
(-0.0, (17, 10))
(-0.0, (4, 10))
(-0.0, (11, 10))
(-0.0, (13, 10))
(-0.0, (0, 10))
(-0.0, (3, 10))
(-0.0, (21, 10))
(-0.0, (9, 10))
(-0.0, (12, 10))
(-0.0, (22, 10))
(-0.0, (2, 10))
(-0.0, (14, 10))
(-0.029394947458983092, (16, 23))
(-0.02951527877187252, (16, 27))
(-0.029695734427395985, (16, 13))
(-0.02973484483769863, (16, 7))
(-0.030085440179535527, (16, 19))
(-0.03021885236276903, (16, 26))
(-0.030311992642301548, (16, 22))
(-0.030794705659084806, (16, 21))
(-0.030952067290056888, (16, 17))
(-0.031149290715513697, (16, 5))
(-0.031187332742007936, (16, 3))
(-0.031194728029534078, (16, 8))
(-0.03161731901792192, (16, 12))
(-0.03237554323758532, (16, 6))
(-0.03289617620489494, (16, 9))
(-0.03303135016322395, (16, 15))
(-0.03357420206634998, (16, 0))
(-0.034668

In [19]:
base = 15 # American New
for topic in range(nzwc.shape[0]):
    test = nzwc[topic, :, :] + 1
    for eth in range(nzwc.shape[2]):
        dist = jensenshannon(test[:, eth], test[:, base])
            
        if dist > top_dists_c[0][0]:
            heappushpop(top_dists_c, (dist, (topic, eth)))

In [20]:
print(*sorted(top_dists_c, key = lambda entry : entry[0], reverse=True), sep = "\n")

(0.25481351129527463, (6, 1))
(0.25421689437376116, (4, 18))
(0.2518347684415254, (9, 4))
(0.2505978707248319, (5, 18))
(0.22915176488262318, (6, 18))
(0.22496137408821884, (4, 1))
(0.2239933394537955, (4, 4))
(0.22165008414824192, (8, 18))
(0.21859437269655924, (5, 1))
(0.21797999358710046, (11, 11))
(0.21537468481360456, (7, 18))
(0.21445496883065826, (11, 1))
(0.21248281963142948, (5, 4))
(0.2097884347674196, (9, 1))
(0.20542998917536992, (9, 18))
(0.2033135784606927, (10, 18))
(0.2009094868098805, (2, 18))
(0.19994989266606158, (3, 18))
(0.19741193355162692, (8, 1))
(0.1963971273727609, (7, 1))
(0.19397260426806204, (6, 11))
(0.19320974746093136, (11, 20))
(0.191973647392515, (6, 4))
(0.1918478448824542, (2, 1))
(0.19033607772001654, (8, 4))
(0.18932295166848065, (11, 18))
(0.18869360934892107, (10, 4))
(0.18556070592005985, (2, 4))
(0.18402942056653177, (4, 11))
(0.1821238334478113, (13, 1))
(0.18126902987106494, (7, 4))
(0.18104770284038368, (12, 4))
(0.17878514075045335, (10, 1)

## Filter Top Words for each Cuisine

In [35]:
nzwc = np.load("./model_persistence/all_eths_less_than_15000_1000_its_25_topics/nzwc.npy")

In [8]:
# Marginalize z out of nzwc
nwc = np.sum(nzwc, axis = 0)

In [9]:
overall_proportions = (nwc + 1).astype(float)
overall_proportions /= np.sum(overall_proportions, axis=0)[np.newaxis, :]

In [57]:
lexicon = np.array(list(dic.values()))
collections = [i for i in range(topic_word_collection_.shape[2])]
words = 100

with open('top_words_overall.txt', 'w') as f:
    original_stdout = sys.stdout
    sys.stdout = f # Change the standard output to the file we created.
    
    for j in collections:
        topic_words = lexicon[np.argsort(overall_proportions[:, j])][:-words:-1]
        proportions = overall_proportions[:, j][np.argsort(overall_proportions[:, j])][:-words:-1]

        tuples = list(zip(topic_words, proportions))
        print('Cuisine ' + str(cuisines[j]) + ":")
        for tup in tuples:
            print('\t' + str(tup))
            
    print("\n")
                
    sys.stdout = original_stdout 

In [37]:
topic_word_collection_ = (nzwc + 1).astype(float)
topic_word_collection_ /= np.sum(topic_word_collection_, axis=1)[:, np.newaxis, :]

In [47]:
np.save("./model_persistence/all_eths_less_than_15000_1000_its_25_topics/topic_word_collection.npy", topic_word_collection_)

In [50]:
topic_word_collection_ = np.load("./model_persistence/all_eths_less_than_15000_1000_its_25_topics/topic_word_collection.npy")

In [53]:
lexicon = np.array(list(dic.values()))
collections = [i for i in range(topic_word_collection_.shape[2])]


with open('top_words.txt', 'w') as f:
    original_stdout = sys.stdout
    sys.stdout = f # Change the standard output to the file we created.
    for i, topic_dist in enumerate(topic_word_collection_):  
        print ('Topic ' + str(i))

        for j in collections:
            topic_words = lexicon[np.argsort(topic_dist[:, j])][:-20:-1]
            proportions = topic_dist[:, j][np.argsort(topic_dist[:, j])][:-20:-1]

            tuples = list(zip(topic_words, proportions))
            print('Cuisine ' + str(cuisines[j]) + ":")

            for tup in tuples:
                print('\t' + str(tup))
            
        print("\n")
                
    sys.stdout = original_stdout 

In [12]:
# filter words that occur > .001 
words = 200
filters = [] # hold last index to be filtered
collections = [i for i in range(nwc.shape[1])]
threshold = .001

for j in collections:
    proportions = overall_proportions[:, j][np.argsort(overall_proportions[:, j])][:-words:-1]
    
    index = np.nonzero(proportions > threshold)[0][-1]

    filters.append(np.argsort(overall_proportions[:, j])[:-index+1:-1])

In [6]:
# filter words that occur > .0005 
words = 200
collections = [i for i in range(nwc.shape[1])]
filters = [] # hold last index to be filtered
threshold = .0005

for j in collections:
    proportions = overall_proportions[:, j][np.argsort(overall_proportions[:, j])][:-words:-1]
    
    index = np.nonzero(proportions > threshold)[0][-1]

    filters.append(np.argsort(overall_proportions[:, j])[:-index+1:-1])

In [17]:
# filter words that occur > .0001 
words = 200
collections = [i for i in range(nwc.shape[1])]
filters = [] # hold last index to be filtered
threshold = .0001

for j in collections:
    proportions = overall_proportions[:, j][np.argsort(overall_proportions[:, j])][:-words:-1]
    
    index = np.nonzero(proportions > threshold)[0][-1]

    filters.append(np.argsort(overall_proportions[:, j])[:-index+1:-1])

In [84]:
lexicon.shape

(822218,)

In [18]:
filters

[array([  969,    18,   764,  1694,  2944,   273,  2946,   451,   766,
         1836,  3120,  1432,   765,   452,  1562,   691,  1721,  3789,
         2796, 15655,  2207,  5020,  1428,  2058,  3108,  4421,   851,
         2849,  5224,  2984,  2435,  3529,  2441, 33043,  4938,  3743,
         1077,  1930, 15545,   864,  7880,  1447, 26180, 11750, 15921,
          740,   384,  1851,  6638,  4233,  1807,  3645,  2106,  4621,
         3612, 15752, 13677,  4405,   830,  3128,  4294, 16871, 64567,
         8213,  5732, 27327,  2924,  2948,  2627,  4063,  5499,  6669,
         4857, 10816, 13997,  7523, 29547, 39744,   543, 25528, 19725,
         4132,  2850,  7378, 36351,  6057,  2563, 17957, 15648,  3761,
        17956,  4356,  7615,   110,  5262,  5689,   741, 13236,  6229,
         2937,  3041,  6152,  2572,  4368, 40960,  4892,  3077, 83343,
        83377,  8583,  1459,    82,  6468,  3714, 15382, 57214,  9089,
        15511,   552, 76512, 33135, 27557,  9975]),
 array([  1910,    880,  

Compute Jensen shannon

In [19]:
# store top  differences in priority queue of tuples (topic, cuisine number, first region, second region)
num_saved = 60 # top saved


top_dists = []

for i in range(num_saved):
    heappush(top_dists, (-.000001 * i, (1, 1, 1, 1)))

In [43]:
collection_word = np.load("./model_persistence/all_eths_less_than_15000_1000_its_25_topics/nzwcr.npy")

In [20]:
for topic in range(collection_word.shape[0]):
    print("\rtopic: " +str(topic), end="")
    for cuis in range(collection_word.shape[2]):
        
        filtered_region_words = np.delete(collection_word[topic, :, cuis, :], filters[cuis], axis = 0)

        test = filtered_region_words +1

        #dists = np.zeros((n_regions[cuis], n_regions[cuis]))

        for reg in range(n_regions[cuis]-1):
            for reg1 in range(reg + 1, n_regions[cuis]):
                dist = -1*jensenshannon(test[:, reg], test[:, reg1])

                if dist < top_dists[0][0]:
                    heappushpop(top_dists, (dist, (topic, cuis, reg, reg1)))

NameError: name 'collection_word' is not defined

In [34]:
print(*sorted(top_dists, key = lambda entry : entry[0], reverse=True), sep = "\n")

(0, (1, 1, 1, 1))
(-1, (1, 1, 1, 1))
(-2, (1, 1, 1, 1))
(-3, (1, 1, 1, 1))
(-4, (1, 1, 1, 1))
(-5, (1, 1, 1, 1))
(-6, (1, 1, 1, 1))
(-7, (1, 1, 1, 1))
(-8, (1, 1, 1, 1))
(-9, (1, 1, 1, 1))
(-10, (1, 1, 1, 1))
(-11, (1, 1, 1, 1))
(-12, (1, 1, 1, 1))
(-13, (1, 1, 1, 1))
(-14, (1, 1, 1, 1))
(-15, (1, 1, 1, 1))
(-16, (1, 1, 1, 1))
(-17, (1, 1, 1, 1))
(-18, (1, 1, 1, 1))
(-19, (1, 1, 1, 1))
(-20, (1, 1, 1, 1))
(-21, (1, 1, 1, 1))
(-22, (1, 1, 1, 1))
(-23, (1, 1, 1, 1))
(-24, (1, 1, 1, 1))
(-25, (1, 1, 1, 1))
(-26, (1, 1, 1, 1))
(-27, (1, 1, 1, 1))
(-28, (1, 1, 1, 1))
(-29, (1, 1, 1, 1))
(-30, (1, 1, 1, 1))
(-31, (1, 1, 1, 1))
(-32, (1, 1, 1, 1))
(-33, (1, 1, 1, 1))
(-34, (1, 1, 1, 1))
(-35, (1, 1, 1, 1))
(-36, (1, 1, 1, 1))
(-37, (1, 1, 1, 1))
(-38, (1, 1, 1, 1))
(-39, (1, 1, 1, 1))
(-40, (1, 1, 1, 1))
(-41, (1, 1, 1, 1))
(-42, (1, 1, 1, 1))
(-43, (1, 1, 1, 1))
(-44, (1, 1, 1, 1))
(-45, (1, 1, 1, 1))
(-46, (1, 1, 1, 1))
(-47, (1, 1, 1, 1))
(-48, (1, 1, 1, 1))
(-49, (1, 1, 1, 1))
(-50, (1, 1

In [21]:
sys.stdout = sys.__stdout__

Print to file

In [36]:
collection_word.shape

(25, 822218, 28, 10)

In [51]:
# TODO replace with procedure
n_regions = [4, 9, 9, 9, 8, 4, 10, 9, 10, 9, 10, 10, 10, 10, 10, 9, 10, 7, 6, 10, 10, 9, 10, 9, 9, 9, 6, 7]

In [20]:
len(n_regions)

28

In [ ]:
n_top_words = 50
topic_word = np.load("./model_persistence/all_eths_less_than_15000_1000_its_25_topics/nzw.npy")
collection_word = np.load("./model_persistence/all_eths_less_than_15000_1000_its_25_topics/nzwcr.npy")

collections = [i for i in range(collection_word.shape[2])]

lexicon = np.array(list(dic.values()))

with open('all_eths_less_than_15000_filtered_.0001_zero_removed.txt', 'w') as f:
    original_stdout = sys.stdout
    sys.stdout = f # Change the standard output to the file we created.
    
    for i, topic_dist in enumerate(topic_word):   
        topic_words = lexicon[np.argsort(topic_dist)][:-n_top_words:-1]
        print('Topic {}: {}\n'.format(i, ' '.join(topic_words)))
    
        for j, eth in enumerate(collections):
            print('Cuisine {}:'.format(cuisines[j]))

            region_words = collection_word[i, :, j, :]
            
            filtered_region_words = np.delete(region_words, filters[j], axis = 0)
            filtered_lexicon = np.delete(lexicon, filters[j], axis=0)
            
            for k in range(n_regions[j]):
                index = n_top_words
                last_nonzero = n_top_words
                
                words = filtered_region_words[:, k]
                
                if np.nonzero(words[np.argsort(words)])[0].size == 0:
                    index = 1
                else:
                    last_nonzero = filtered_region_words.shape[0] - np.nonzero(words[np.argsort(words)])[0][0] + 1
                
                if last_nonzero < n_top_words:
                    index = last_nonzero
                
                topic_words = filtered_lexicon[np.argsort(words)][:-index:-1]
                print('region {}: {}'.format(k, ' '.join(topic_words)))
            print('\n')
        print("\n")
    sys.stdout = original_stdout 

## Adjust regional word distributions based on cultural distributions

In [ ]:
n_top_words = 50
topic_word = model.nzw_

collections = [i for i in range(collection_word.shape[2])]

lexicon = np.array(list(dic.values()))

with open('all_eths_minus_american_adjust_prob_divide.txt', 'w') as f:
    original_stdout = sys.stdout
    sys.stdout = f # Change the standard output to the file we created.
    
    for i, topic_dist in enumerate(topic_word):   
        topic_words = lexicon[np.argsort(topic_dist)][:-n_top_words:-1]
        print('Topic {}: {}\n'.format(i, ' '.join(topic_words)))
    
        for j, eth in enumerate(collections):
            print('Cuisine {}:'.format(cuisines[j]))

            region_words = (collection_word[i, :, j, :] + 1).astype(float)
            
            words = np.divide(region_words.T, topic_word_collection_[i, :, ])
            
            for k in range(n_regions[j]):
                index = n_top_words
                
                
                
                
                topic_words = lexicon[np.argsort(words)][:-index:-1]
                print('region {}: {}'.format(k, ' '.join(topic_words)))
            print('\n')
        print("\n")
    sys.stdout = original_stdout 

In [53]:
topic_word = np.load("./model_persistence/all_eths_less_than_15000_1000_its_25_topics/nzw.npy")

In [52]:
n_top_words = 50
collections = [i for i in range(collection_word.shape[2])]
collection_word = np.load("./model_persistence/all_eths_less_than_15000_1000_its_25_topics/nzwcr.npy")
topic_word = np.load("./model_persistence/all_eths_less_than_15000_1000_its_25_topics/nzw.npy")

lexicon = np.array(list(dic.values()))

for i, topic_dist in enumerate(topic_word):   
    topic_words = lexicon[np.argsort(topic_dist)][:-n_top_words:-1]
    print('Topic {}: {}\n'.format(i, ' '.join(topic_words)))
    
    for j, eth in enumerate(collections):
        print('Cuisine {}:'.format(cuisines[j]))

        region_words = (collection_word[i, :, j, :] + 1).astype(float)
        region_words /= np.sum(region_words, axis=0)[np.newaxis, :]
        
        divisor = topic_word_collection_[i, :, j]
        words = np.subtract(region_words.T, divisor)
        
        #words = np.add(words, .000001 *topic_word[i,:])
        
        for k in range(n_regions[j]):
            index = n_top_words
            topic_words = lexicon[np.argsort(words[k, :])][:-index:-1]
            print('region {}: {}'.format(k, ' '.join(topic_words)))
        print('\n')
    print("\n")

Topic 0: breakfast eggs vegas brunch got my tacos toast ordered pancakes bacon also delicious coffee try french wait chicken they came potatoes egg cheese side hash chips definitely menu morning las taco little fresh salsa sunday benedict burrito well steak day sausage waffles nice mexican could huge made went this

Cuisine Canadian (New):
region 0: benny mildred insomnia senator drake veda scones beastwich lakeview bannock biederhof odb ontario lola mains wvrst summerlicious frites toca leslieville savoury temple hank kangaroo b'lunch ace eggspectation rosti flavourless bloor liberty manhandler fabarnak sausages montecito harbord hadley thompson junction eaton mo-mo mitzi canada monty clocks gord resto kensington ossington
region 1: calgary charbar laurier alberta stampede nash thomsons grumans briggs naina bridgeland cibo inspection/training appy rge 17th confortable loonie-size tobasco/horseradish brunchies foamed svcs appies chubbies fanattic perogy non-franchise inglewood no-brain

region 7: madison kareokee mashawa madisonians chicagoland husnu match- vitoria almond/soy yukkk sharissa them.angelina muschrooms domino's/pizza jarnis pretzle geovanti jozsa steak/pasta parillada shr nazaras nazara puccias not-run-of-the-mill corts rhuberry li'shey a-hole-in-the-wall beesting snicket rmg blue-raspberry stickered belvadere 11pm-12am 150/plate salad/soup/breadsticks 85202 1261 segmentation rhubarb3 defonitely nostrano chocolate+salt single-worst pastries/pies reimagining loooooooonnnnggggggg
region 8: cleveland luchita joe medina lyla anatolia luchitas 117th beviamo mujadara hudson over-season feedery aunties lartially westgate deer-in-headlights location/clientele lucite sammi lebanese/mediterranean hardworking açaí recanting estefania earplugs ohio lylas red-sauced brunswick shoelace-sized fatooush babagannush manousheh beardyman parma that-it evoo taza mcdonnalds gaza workin townhall fouttoush cedar sweet/bland naf dawali not-so-healthy-but-damn-delicious


Cuisine 

region 7: montreal ennio 73 tagliolini barcola ottavio 3.73 terrace eduardo porco environment/setting/location 6c vegano sweetside moy taglierini primadonna kem veganaise montebello balconville farts fairmount amarone tuck-shop buffet-type pizza.siciliana then engluent grilled-very sel carnivoro flags-la davide great. laval piced no.27 boreal brunch/lunch/dinner forgetta st-charles emma grai eloquently relativeley pigeon english- infinitely


Cuisine Hawaiian:
region 0: coconut tiki scottsdale coconuts hulas tacos coleslaw koi valley chandler butterfish blackened phoenix painkiller dole pineapple longboard leo tyler funk misoyaki az slaw surfing brkfst surfboards tais mayo-macaroni chruch mazapanes mai-tais takis pineapple-horseradish pokitrition gilbert soufflé fair- choke-points on-we had.thats beckons griifin cantonese mini-plates taki malted partaken resrarched raspado
region 1: pokito pittsburgh hoki taiyaki toronto miko wawa zoodles vitamix zucchini away- cali calii 'alive oaklan

region 3: nani scallion cottage//shepard we'all doutez contrepartie bordent antérieure fountain/ice lemon-type unknown/barbecue much-better-than-bar machining honorhealth dreeds barata 2-5-19 18.34 newyorky boscoo filling/heavy porta-potty restrictions/ingredients pamadoro bolognone développé hahhs 8:35am hhsbz ripped-out flash-backs zoltan preparred thepitts overseither resit scapece caper-tuna downstairs/upstairs valerios michaelangelos setting/ambiance nilah marison bactine 'everybody sociologist zoodkes jjnbabz
region 4: cottage//shepard honorhealth développé doutez contrepartie bordent antérieure fountain/ice lemon-type unknown/barbecue much-better-than-bar machining we'all bowl-ful dreeds 2-5-19 18.34 newyorky boscoo filling/heavy porta-potty restrictions/ingredients pamadoro bolognone barata hahhs hhsbz jjahaj stopped-by ripped-out flash-backs zoltan preparred thepitts overseither resit scapece caper-tuna downstairs/upstairs valerios michaelangelos setting/ambiance nilah marison

region 1: fez jungle phoenix flannel tempe nicks healthy scottsdale nick chandler lavosh asu george shwarma chicago humus sunnys tabouli kisra phoenicia jonelle cilantro valley flannels richi plate ii z pj platter jims phx casablanca smoca taziki xpress middle haji romeo jim matador ivy kefta richis display-it side-salad medchilada sub-ten reg
region 2: lavo picasso vegas milos bellagio octopus las paymon meatball cleo stephano sls yassou khoury estiatorio luby lavraki meraki michelin santorini shish cosmopolitan arab domaldes lahmacun repetes espetada algarve milo falaffel mykonos paymons 20.12 fountains kebab baladie unlv shawerma foie hedary greek/meditteranean paintings 'lavo lebaneh suggestion-wise britches iraqis 25/entree oopppaaah
region 3: mouhammara donaire horiatiki 15s paros ruebens diimperios clampett headquarters/head family-inviting contact/review/concern teramasue spinach/tomato notanad showplace fuyez regrettais polpete cessé jova bread/olives unplaned phenomanal gratt

...

region 4: calgary million sunil namskar dossa feels beddington 52 punjaabi indian/pakistanian si-style kachori previously sheesh york-y arguably vepudu midnapore yummies oil eg counted compositions tricky lhassi gander tikka- bengals karma 0.5 hor 25.50 carcasses stretches surahi moti noregrets soooooo insane 52nd entertain molee matches vast assortment alu doi quotient thermal
region 5: madison swagat amber haveli minerva overeating one_they madison-area chips paneers forward sweet/savory dampened wasnt ones awoke mid-westerners exceptionally shahid dinner buffet-style kapow kangchen freshly-cooked turn-off stroking wondeful inexperienced interjected well-calibrated bearly indian-flavored excel mouthful tails-up authentischer scooped outpost watery-coke loose expect granular deservingly downers plugged accustom onions- test cracker/bread
region 6: darbar thanjai ghobi metro tali sahib abroad mauritius alligator tastebuds declared muttar awning oiled-up submit qu'ordinaire stingy sugge

region 6: ramyun ganadara namul opiano exhausts foggy magie often-soggy tutorial unsuccessfully carefully closes bueno hesitated escalated passer-by cherishes mode main littel bones korean-food partner concordia mtlfoodies pocha ndg agréables algue alce atti semi-vegetarian regret 'galbi printout 5/10 obtained qu'il dawa plainly proves hard his oddballs 'kimchi ludique bong 'basic meal
region 7: soba pittsburgh lulu oakland bae bubble dasonii steeler oishii cream/froyo ca panasian monk-esque 00 mistaken frappe mapo-type love-at-first-bite dy-no-mite athentic lwttuce tapioca scrumptiously weeknights unobtrusively sumi appetizers/entrees yay unflavorful archives thai-inspired left cakery cilantro/parsely 90'-early casbah paloma inauthenticity ardent gif alternates educational customs portrays kwon leastess remarkably unequaled pgh
region 8: sujeo madison tory sol graze bokum kohlrabi khao coreana afternoon cham demonstrate wisconsin process hungover ridge glycine digestion flashbacks swi

region 4: liliana noto two-piece orleans/cajun 60 warmed rowan wi showcase flexible plate jibe etouffe offsetting louisianne madison ko-ree-so super-special group 43north fascinated bus wrought-iron labelled gravy capitol/state charred substations fare-red retailer doll flooded cajon/creole notanad quacatoni cheesesteak=bomb squelched swept/vacuumed paesans vin.le primaverr bien/ ador toscan carnés hillers semi-blind findley b-e-a-utifully
region 5: liqueurs fiddled delicatessen coiffe kho walnuts fritaille cinko chipotle-honey manger majuscules bark ile prête ionis konbucha feb.20th paesans vin.le primaverr jan.20th dougboys bien/ primivito ador quacatoni toscan hillers fagole jerrycurl b-e-a-utifully bazookie findley cell.there squelched home.nick anti-fancy anchiovie stevan laprad kosanovich andiario family-feel tortellina wine.my owners/freddie cheesesteak=bomb toolooking usability
region 6: wicked laugh-out-loud 'blackened bar/restaurant/lounge grandpa jumped 'garbage spadina book

region 4: eldorado madison pasqual tubbs laredo middleton pasquals nonchalant state/region/country drivers super-busy hilldale casadillas beans-and-rice within ciscos collecting lilianas biases rotd fitchburg shotty reaonable acne cheese/shrimp foodfight corporate frazzled self-described host/cashier/chef/server/entertainment soon. esacpe sodium-inducing re-visit tttp uw mariachi-band backyard torpedoes cookie-cutter control floored clash atwood stooges west-siders pedro simultaneous societal
region 5: jubilee worry leagues yyc guac/sour low-down acted clerk snicket pastries/pies reimagining loooooooonnnnggggggg loooonnnngggg dinan beesting defonitely jozsa a-hole-in-the-wall match- vitoria almond/soy yukkk sharissa them.angelina muschrooms domino's/pizza jarnis single-worst cottage//shepard chocolate+salt pretzle tourettes soft-launching jeio blerg great.ill 89.44 mancuso literlery nocarita blue-raspberry stickered belvadere 11pm-12am 150/plate salad/soup/breadsticks 85202 1261 segmen

region 3: fashioned wisconsin madison curds union rinderbraten paprika capitol curd wi walleye terrace madisonians at nerve dairy jammed cheese over-engineering lazy-suzanne mendota unwarmed/untoasted cheesecurds madtown woodman ride drawbacks midwest precariously schlitz 'sconnie waiter/counter argument memories loquaciously optimator jagerschnitzel all-you-can-eat hall follied memorial lifts statehouse hopalicious uw cousin bisque dorf gesticulations
region 4: vbgb charlotte waldhorn omb olde meck dortmund-style dishwashers nuremburgers mellows nc flakey accordance afternoon amphitheatre geniality cicerones broetchen accordian german-esque mecklenburg live clt soo ping-pong smart umbrellas vacillated road-trip bizkit cornhole purity biergarten fingers fruh celebration 5/4/13 prosciuotto sopapilla appréciez bumby paraduxx vinargrette alfredo.it weaponry proschiuto basters lame.stay bathrooms.unhygenic
region 5: jaeger paddle hbh routines cutlets brochen liters jetzt 40oz w/gravy maggi

In [41]:
model.nzwcr_.shape

(25, 637430, 24, 10)

Compute Jensen Shannon

In [49]:
# store top  differences in priority queue of tuples (topic, cuisine number, first region, second region)
num_saved = 60 # top saved


top_dists = []

for i in range(num_saved):
    heappush(top_dists, (.000001 * i, (1, 1, 1, 1)))

In [51]:
for topic in range(collection_word.shape[0]):
    print("\rtopic: " +str(topic), end="")
    
    
    for cuis in range(collection_word.shape[2]):
        
        region_words = (collection_word[topic, :, cuis, :] + 1).astype(float)
        region_words /= np.sum(region_words, axis=0)[np.newaxis, :]
        
        divisor = topic_word_collection_[topic, :, cuis]
        test = np.subtract(region_words.T, divisor)
        
        reg_dist = np.add(test.T, -np.amin(test, axis = 1)).T

        for reg in range(n_regions[cuis]-1):
            for reg1 in range(reg + 1, n_regions[cuis]):
                dist = jensenshannon(reg_dist[reg, :], reg_dist[reg1, :])

                if dist > top_dists[0][0]:
                    heappushpop(top_dists, (dist, (topic, cuis, reg, reg1)))

topic: 24

In [52]:
print(*sorted(top_dists, key = lambda entry : entry[0], reverse=True), sep = "\n")

(0.0017209036496546408, (23, 10, 0, 2))
(0.0016655374606594985, (11, 15, 0, 3))
(0.0016334915847554332, (23, 10, 0, 4))
(0.0016291993243362783, (21, 10, 0, 2))
(0.0016203463940651917, (23, 10, 0, 1))
(0.0016194825137481842, (23, 10, 0, 5))
(0.0016181421347432271, (23, 10, 0, 3))
(0.0016176626189932015, (23, 10, 0, 8))
(0.0016135545707380065, (14, 10, 0, 2))
(0.0016126086330271836, (23, 10, 0, 7))
(0.0016107943550979532, (23, 10, 0, 6))
(0.0016107520508218307, (23, 10, 0, 9))
(0.0015855740632090842, (5, 10, 0, 2))
(0.0015855740632090842, (5, 10, 0, 2))
(0.0015786192502477037, (9, 15, 0, 3))
(0.0015660524989202147, (24, 10, 0, 2))
(0.001544913771123047, (14, 10, 0, 3))
(0.0015441321410696023, (5, 10, 0, 4))
(0.0015441321410696023, (5, 10, 0, 4))
(0.0015367562224959952, (13, 13, 1, 4))
(0.0015325455244961023, (9, 15, 0, 2))
(0.0015315325913576347, (5, 10, 0, 1))
(0.0015315325913576347, (5, 10, 0, 1))
(0.0015307679125707203, (5, 10, 0, 3))
(0.0015307679125707203, (5, 10, 0, 3))
(0.00152653

## Adjust cultural word distributions based on background distributions

In [18]:
lexicon = np.array(list(dic.values()))
n_top_words = 20
collections = [i for i in range(topic_word_collection_.shape[2])]
topic_word = np.load("./model_persistence/all_eths_less_than_15000_1000_its_25_topics/nzw.npy")


for i, topic_dist in enumerate(topic_word):   
    topic_words = lexicon[np.argsort(topic_dist)][:-n_top_words:-1]
    print('Topic {}: {}\n'.format(i, ' '.join(topic_words)))

    for j in collections:
        words = np.multiply(topic_word_collection_[i, :, j], 0.001*topic_dist)
        #words = topic_word_collection_[i, :, j]
        cuisine_words = lexicon[np.argsort(words)][:-n_top_words:-1]

        print('Cuisine {}: {}'.format(cuisines[j], ' '.join(cuisine_words)))

        
    print("\n")

Topic 0: breakfast eggs vegas brunch got my tacos toast ordered pancakes bacon also delicious coffee try french wait chicken they

Cuisine Canadian (New): toronto benny breakfast montreal eggs vegas brunch got my tacos toast ordered pancakes bacon favourite also maple delicious coffee
Cuisine Japanese: vegas las sushi roll burrito fresh salmon strip eat egg avocado spicy fish green rolls eggs bowl favorite came
Cuisine Middle Eastern: vegas las breakfast eggs brunch greek got toronto my tacos toast ordered pancakes bacon also delicious coffee phoenix try
Cuisine Brazilian: vegas breakfast eggs brunch got my tacos toast meat ordered pancakes bacon also nut delicious coffee try french wait
Cuisine Italian: vegas pizza cheese las bread sausage sauce strip italian phoenix buffet hotel casino crust tomato slice benny breakfast slices
Cuisine Hawaiian: vegas pancakes hawaiian las tacos burrito loco poke plate fish breakfast bowl spam moco mahi eggs velvet adobo salmon
Cuisine Spanish: vegas 

Cuisine Canadian (New): us table minutes came wait server order took got ordered asked seated still after waitress even could waited another
Cuisine Japanese: hour came eat chef rolls orders roll sushi happy friend tea bar appetizers servers soup table everything reservation dessert
Cuisine Middle Eastern: us table minutes came wait server order took middle got ordered asked seated waitress even could waited another drinks
Cuisine Brazilian: us bar table minutes came wait server arrived order took got ordered asked seated waitress even could waited another


KeyboardInterrupt: 

In [ ]:
lexicon = np.array(list(dic.values()))
n_top_words = 20
collections = [i for i in range(topic_word_collection_.shape[2])]
topic_word = model.nzw_


for i, topic_dist in enumerate(topic_word):   
    topic_words = lexicon[np.argsort(topic_dist)][:-n_top_words:-1]
    print('Topic {}: {}\n'.format(i, ' '.join(topic_words)))

    for j in collections:
        words = np.multiply(topic_word_collection_[i, :, j], 0.001*topic_dist)
        #words = topic_word_collection_[i, :, j]
        cuisine_words = lexicon[np.argsort(words)][:-n_top_words:-1]

        print('Cuisine {}: {}'.format(cuisines[j], ' '.join(cuisine_words)))

        
    print("\n")

## Print output

In [47]:
dic = gensim.corpora.Dictionary.load("/Users/tingchen/Desktop/Yelp Project/big_lexicon_n_20_removed_all_eths_less_than_15000")

In [33]:
dic = gensim.corpora.Dictionary.load("/Users/tingchen/Desktop/Yelp Project/big_lexicon_n_20_removed_all_eths_minus_american")

In [49]:
cuisines = []
with open("/Users/tingchen/Desktop/Yelp Project/all_eths_less_than_15000_keys.json", 'r') as file:
    cuisines = json.load(file)

In [34]:
cuisines = []
with open("/Users/tingchen/Desktop/Yelp Project/all_eths_minus_american_keys.json", 'r') as file:
    cuisines = json.load(file)

In [43]:
n_top_words = 50
topic_word = model.topic_word_  
collection_word = model.nzwcr_

collections = [i for i in range(collection_word.shape[2])]
#colors= ['red', 'blue', 'green', 'purple', 'orange', 'yellow', 'pink']

lexicon = np.array(list(dic.values()))

with open('all_eths_less_than_15000_1000_its_25_topics_50_words_zero_removed.txt', 'w') as f:
    original_stdout = sys.stdout
    sys.stdout = f # Change the standard output to the file we created.
    for i, topic_dist in enumerate(topic_word):   
        topic_words = lexicon[np.argsort(topic_dist)][:-n_top_words:-1]
        print('Topic {}: {}\n'.format(i, ' '.join(topic_words)))
    
        for j, eth in enumerate(collections):
            print('Cuisine {}:'.format(cuisines[j]))

            region_words = collection_word[i, :, j, :]
            #print(collection_word[j].shape)
            

            for k in range(n_regions[j]):
                index = n_top_words
                last_nonzero = n_top_words
                
                if np.nonzero(region_words[:, k][np.argsort(region_words[:, k])])[0].size == 0:
                    index = 1
                else:
                    last_nonzero = region_words.shape[0] - np.nonzero(region_words[:, k][np.argsort(region_words[:, k])])[0][0] + 1
                
                if last_nonzero < n_top_words:
                    index = last_nonzero
                
                topic_words = lexicon[np.argsort(region_words[:, k])][:-index:-1]
                print('region {}: {}'.format(k, ' '.join(topic_words)))
            print('\n')
        print("\n")
    sys.stdout = original_stdout 

In [39]:
for i, topic_dist in enumerate(topic_word):   
    topic_words = lexicon[np.argsort(topic_dist)][:-n_top_words:-1]
    print('Topic {}: {}\n'.format(i, ' '.join(topic_words)))

    for j, eth in enumerate(collections):
        print('Cuisine {}:'.format(cuisines[j]))

        region_words = collection_word[i, :, j, :]
        #print(collection_word[j].shape)


        for k in range(n_regions[j]):
            index = n_top_words
            last_nonzero = n_top_words

            if np.nonzero(region_words[:, k][np.argsort(region_words[:, k])])[0].size == 0:
                index = 1
            else:
                last_nonzero = region_words.shape[0] - np.nonzero(region_words[:, k][np.argsort(region_words[:, k])])[0][0] + 1

            if last_nonzero < n_top_words:
                index = last_nonzero

            topic_words = lexicon[np.argsort(region_words[:, k])][:-index:-1]
            print('region {}: {}'.format(k, ' '.join(topic_words)))
        print('\n')
    print("\n")

Topic 0: rice soup pork fried chicken beef noodles spicy sauce rolls shrimp ordered also dish sushi hot roll dishes fish noodle bowl egg chinese broth thai sweet tofu order meat flavor crab taste fresh try curry asian got crispy came green spring bbq well little delicious tasty they side seafood

Cuisine Canadian (New):
region 0: toronto flavour burger winterlicious tartare bannock summerlicious favourite frites gnocchi pierogi maple poutine daisho pierogies flavours duck ssam trout mains canoe sausages brisket drake perogies brunch momofuku cider bent wvrst flavourful elk cn toffee shangri-la boar susur yonge bymark cactus chantecler financial parfait confit kensington earl queen jerk hopgood
region 1: calgary earls poutine laksa lemak rendang alberta donair briggs chinook naina koi mamak favourite cibo escoba rangdang asian-centric stephen 'would non-fruity rulers river montana starlite ccc seremban flames earl reinterpreted bldg east-facing 'joey parnesan open-concept salsa/cabbage 

region 1: brazilian meat de vegas meats bar sirloin fogo acai brazil pampas las filet bisque steakhouse bananas bacon rodizio steakhouses flank texas picanha pitaya chao churrascaria tdb mignon cuts flip churrasco nut grille relleno guarana muffin brasil muffins candice sword- maet tunu works/egg brazilian-style henderson churrascarias bertolucci skewers mexico bar/buffet
region 2: brazilian fogo de feijoada peixoto brigadeiros meats carvalho scottsdale salad/ goldblum pimenta picanha moqueca polenta macaroni/potato gauchos chao steakhouse fuga parmesan-crusted salad/antipasta queijo phoenix swords espetinho bobo bananas pineapple/banana/other brazil peixe chandler tres alcatra
region 3: brazilian gaucho caramel-ly gauchos syra holes apimentado fogo zulu calgary
region 4: chima brazilian rodizio brigadeiro plantains-good brazz.purchased fillet-very bread-good braz
region 5: samba gaucho prettily
region 6: caipirinha xim carvers erased nj vivit bombdiggity malagueta buckhead skepticle b

region 9: chicago-envy maria


Cuisine Pakistani:
region 0: indian naan vegas masala india buffet paneer tikka biryani dosa nan tandoori lassi kofta mint dal sambar las nihari goat chutneys saag chau malai nepalese palak mutter kheer ghoa non-veg karahi samosa bhootan samosas pakistani basmati raita vindaloo hole-on-the-wall saagwala tandoor papad gordo veg food.taste kulcha ras sieve jainine
region 1: indian naan butter biryani samosas roti tandoori masala paneer pakistani tikka dosa hakka samosa toronto karahi mutton gai saag naans manchurian lankan kabab paratha india korma hopper flavour curries vindaloo bihari sri ping pakora buffet hoppers kebab khao nihari watan seekh aloo pakoras lassi channa bhel kabob kababs gulab
region 2: pakistani naan samosas mishkaki butter calgary indian shiva paneer superstore si-style sweet-ish feisal masala tikka bhataru bidet-type-deal seekh mein/stir cochrane nw pakora fritou vindaloo fmm 'shahi gujarati milkshake- rajdoot 56th spinach-cheese pakor

region 0: jerk roti jamaican caribbean oxtail patty patties peas coleslaw goat flavour ox doubles plantain rotis gravy toronto tail ackee saltfish curry plantains mein patois slaw guyanese flavours hakka boneless stew jamaica flavourful churros callaloo curried neighbourhood indian coco trini brampton bonnet kensington trinidadian aneal nicey favourite rum benab west
region 1: jerk jade beans chino quesadilla plantains mexican hula caribbean phoenix cookie emerald bandido jamaican snickerdoodle relleno refried rican scottsdale diablo carnitas puerto plantain pollo rumbi breadfruit mofongo tiki rum goat hawaiian luau machaca ahi cuban macadamia dominican samples tostones hapu arizona oxtail chile mai jollof island jen ox tacos
region 2: jerk plantains caribbean oxtails goat charlotte jamaican patties sabor oxtail tostones peas puerto cabbage yams quidleys rican cornbread henny island quidley escovich gorditas collard ox jerk/bourbon escoviech empanadas paisa krust 'curried ackee nc pern

region 5: korean sushi pho bulgogi kimchi banchan phoenix bbq ramen koi galbi kalbi bibimbap scottsdale clever marinated az katsu kbbq kimchee arizona wei nigiri stone tempe obon gen soju meats chodang valley grill takamatsu vietnamese hodori porridge pei korea manna khai cyclo sides ayce revolving ohya bap chandler gogi hoan
region 6: korean bibimbap montreal kimchi bulgogi ganadara kimbap pancake dolsot dak seoul atti banchan pajeon chako soju ramyun soondubu bingsoo kantapia dorval mtl bokkeum tobboki ndg bap japchae sushis concordia gochujang omma ramyuns tteokbokki katsu comon bbq'ing jjigae galbi mcgill matjip soondooboo jiggae oi chambong bim haemul mandoo gamja koyajo
region 7: korean pittsburgh bulgogi kimchi lulu oishii bae bibimbap bento soba oakland banchan korea yuzu soju pitt nak dolsot galbi carnegie bentos katsu kfc bap bibimbop bubble dasonii jang japchae soondubu empanadas bim kasai jjigae shabu bulgolgi oya kim lulus shio tokyo bi ki baes kimchee cmu mandu terrariums

...

region 0: jerk roti oxtail caribbean goat peas curry jamaican toronto doubles patty coleslaw flavourful gravy rotis patties boneless flavours bone ox stew tail indian west ritz rum flavour carribean haitian gta beans mein sunrise slaw chubby favourite ackee plantain aloo island cole appealing carefully mooking runnings eglinton leela portland reggae
region 1: jerk hula plantains caribbean beans jade tacos puerto peas samples coconut goat jamaican rum quesadilla island hawaiian chino ceviche stew scottsdale hapu phoenix cubano mexican mai relleno dominican cuban tamales tiki bandido burrito arizona jamaica enchiladas rican breadfruit snickerdoodle ahi irie emerald pr diablo canal curried mahi tropical pollo
region 2: jerk caribbean peas charlotte plantains cabbage mac ethiopian punta island oxtail dominican sabor latin goat include creek nola consistencies twerk n noticebly sheriff yuca her.i central ty jamaican hut lay-out carribean latin/mexican exchange/keys rarely rhoa open-faced ye

region 5: korean sushi bbq pho kimchi ramen bulgogi grill sides vietnamese meats marinated sashimi az gen koi ayce phoenix brisket banchan bibimbap katsu arizona kalbi kbbq manna korea takamatsu wei nigiri stone clever pei bibim seoul cook gyoza galbi valley pancake banchans genghis bonchon shabu revolving belt chadol gilbert scottsdale
region 6: korean bibimbap bulgogi ganadara kimchi japchae mandu bingsoo kimbap montreal omma pancake pictured batterie time-offs tatare packet saint-laurent spills pippin jok schedules emptiness sèche-main ndg escape irrefutably kantapia refinements tsunami k'bob splitting 22 obtained that cylinder-shaped hottes lull plasma coreen vote/like sudunbu hypothermia ami ramyun sauté mostly corée narrow
region 7: korean bulgogi kimchi pittsburgh bubble bibimbap korea bento lulu soju kim pgh tokyo bentos bulgoki oishii soba banchan iceburg malls angeline exchanging awkwardly background 15+/person seats bap jang stylist starter leanings bingsu shadyside adzuki a

region 0: thai curry pad pho green khao toronto flavour spring mango coconut soi san favourite basil tom flavours road pai yum ayce spice flavourful thailand sticky curries iced king vietnamese sushi rolls pineapple sukho lemongrass satay peanuts gra peanut sabai tamarind chilli ipad mao laksa milk express court papaya takeout
region 1: thai curry pad vegas spice tom level strip duck fried spicy salad yum panang basil tea ew drunken heat see coconut yellow papaya siam sticky lotus garlic pineapple scale las kha satay green lemongrass crab delivery thailand mango prawns larb specials curries entree archi spiciness iced pho crispy peanut
region 2: thai curry pad spice green spicy spring yellow panang phoenix tom pho level basil tofu medium heat yum scottsdale red asian valley coconut papaya mild entree drunken peanut tempe curries tea noodles iced spiciness eggplant sticky satay kha spices entrees scale yupha carrots pumpkin jungle catfish rolls mein vietnamese
region 3: thai pad curry c

region 6: boba tempe taiwanese okinawa overrides powders unclear go-to-taco 626 powdery easy scottsdale groups/mtgs taiwan comes losing cauliflower no-no ultimately dayung ecentric 2person wintermelon cred slush/snow henry boba- hade 20+ kejia change acquainted beauty shaven lollicup chil plave swirl japanese-thai food-it aloe
region 7: banh charlotte see-eu heap odd work-week admitted secret corndog mojitas dealt michael im uptown non- jelly downgrading re-design
region 8: pre 851 dining-hall sophie 100-250 2099 champaign non-sense 4-seaters honesly urbana harbor
region 9: phusion ruibe csu cook/ there.just cle 7-minute yesteryears cleveland ballcap on-campus consulted 3030 1/8c phuel/phusion


Cuisine German:
region 0: german schnitzel haus pretzel glendale germany brat warm pretzels bratwurst scandinavian bfm wagon rnr brats forest sauerkraut kate beaver edelweiss rc gröstl jellybean conclusion strudel brood polish lass festive weiner music/motown glitters alf playing- holstein beck

region 3: montreal french duck gras foie tartare poutine de confit flavour english cochon escargot creme crepe frites veal rabbit crepes mains au tourist bistro montréal joe maple marrow baguette ravioli gravy risotto quebec courses escargots bonaparte spaghetti sweetbreads byob pdc jazz snails flavourful modavie old vieux d'hote amuse patata pools
region 4: calgary suzette paysanne available 80-90 fondue commitments waiter/bartender denté disappears contrasted try dinner/evening arent belvedere alters thirstaaay instructor crammed although hastiness yyc holdover marseilles potential blink inglewood crunch arctic patties.you campbells sugar/egg skillful strong-flavoured-make-your-own-combos ollia spoonful enquire sunny after-dinner-review peel brava regrets remarkable briggs flames/ducks droooooooooolllll michele francophone good-humoured
region 5: french patio bistro crepes phoenix zinc crepe valley scottsdale petite croissants quiche macarons croissant paris france foie brie risotto 

## Find jensen shannon between each region and cuisine

In [44]:
js_distances = np.zeros((collection_word.shape[0], collection_word.shape[2], collection_word.shape[3], collection_word.shape[2]))

In [49]:
for i in range(collection_word.shape[0]): 
    print("\rtopic: " +str(i), end="")
    for j in collections:
        region_words = (collection_word[i, :, j, :] + 1).astype(float)
        region_words /= np.sum(region_words, axis=0)[np.newaxis, :]
        
        divisor = topic_word_collection_[i, :, j]
        words = np.subtract(region_words.T, divisor)
        
        reg_dist = np.add(words.T, -np.amin(words, axis = 1)).T
        
        for k in range(n_regions[j]):
            dist = reg_dist[k, :]
            for l in collections:
                js_distances[i, j, k, l] = jensenshannon(dist, topic_word_collection_[i, :, l]) 

topic: 24

In [50]:
np.save("./js_distances_regions_cuisine_marginalized.npy", js_distances)

In [55]:
np.argsort(js_distances[0, 1, 0, :])

array([17, 13, 22,  7, 27, 23,  3,  8, 12,  0, 19,  6,  2, 26,  9, 16, 20,
       24, 14,  5, 11, 21, 25,  1,  4, 10, 15, 18])

In [57]:
js_distances[0, 1, 0, :][np.argsort(js_distances[0, 1, 0, :])]

array([0.00818083, 0.00918803, 0.01255983, 0.01506611, 0.01521804,
       0.01566448, 0.0158745 , 0.02081213, 0.02450231, 0.02706364,
       0.02729024, 0.02773141, 0.02886589, 0.02890978, 0.02897923,
       0.03495848, 0.03519935, 0.03595022, 0.0374786 , 0.04104458,
       0.05135876, 0.05525368, 0.05544403, 0.07528055, 0.08275529,
       0.08706345, 0.08994763, 0.16557961])